# HW Topic Modeling

## Section 1: Data Acquisition

In [1]:
import csv
import pandas as pd

# import packages for text processing
import nltk
from nltk.corpus import stopwords
from nltk.stem.wordnet import WordNetLemmatizer
from nltk.stem.porter import PorterStemmer
import re

import gensim
from gensim.corpora import Dictionary
from gensim.models import ldamodel
from gensim import corpora, models, similarities

from gensim.models.coherencemodel import CoherenceModel
from gensim.models.wrappers import LdaVowpalWabbit, LdaMallet

import numpy
import matplotlib.pyplot as plt
%matplotlib inline

import warnings
warnings.filterwarnings('ignore')  # To ignore all warnings that arise here to enhance clarity

C:\Users\Eric\AppData\Local\Continuum\anaconda2\lib\site-packages\gensim\utils.py:1212: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


## Make the processes visible

In [2]:
#https://radimrehurek.com/gensim/tutorial.html
# this makes process visible

import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

## Import data

In [12]:
texts = []
counter = 0
r = csv.reader(open('data/fake.csv', 'rb'))
while counter < 1501:
    for i in r:
        counter+=1
        texts.append(i)  
len(texts)

17949

In [14]:
#first two rows
texts[1:3]

[['6a175f46bcd24d39b3e962ad0f29936721db70db',
  '0',
  'Barracuda Brigade',
  '2016-10-26T21:41:00.000+03:00',
  'Muslims BUSTED: They Stole Millions In Gov\xe2\x80\x99t Benefits',
  'Print They should pay all the back all the money plus interest. The entire family and everyone who came in with them need to be deported asap. Why did it take two years to bust them? \nHere we go again \xe2\x80\xa6another group stealing from the government and taxpayers! A group of Somalis stole over four million in government benefits over just 10 months! \nWe\xe2\x80\x99ve reported on numerous cases like this one where the Muslim refugees/immigrants commit fraud by scamming our system\xe2\x80\xa6It\xe2\x80\x99s way out of control! More Related',
  'english',
  '2016-10-27T01:49:27.168+03:00',
  '100percentfedup.com',
  'US',
  '25689',
  'Muslims BUSTED: They Stole Millions In Gov\xe2\x80\x99t Benefits',
  '0',
  'http://bb4sp.com/wp-content/uploads/2016/10/Fullscreen-capture-10262016-83501-AM.bmp.jpg',

## Section 2: Text Preprocessing

### Section 2.1: Removing stopwords and cleaning the text

In [15]:
# Remove useless numbers and alphanumerical words
documents = [re.sub("[^a-zA-Z]+", " ", str(text)) for text in texts]

# tokenize
texts = [[word for word in text.lower().split() ] for text in documents]

# stemming words: having --> have; friends --> friend
lmtzr = WordNetLemmatizer()
texts = [[lmtzr.lemmatize(word) for word in text ] for text in texts]

#porter_stemmer = PorterStemmer()
#texts = [[porter_stemmer.stem(word) for word in text ] for text in texts]

# remove common words 
stoplist = stopwords.words('english')
texts = [[word for word in text if word not in stoplist] for text in texts]

#remove short words
texts = [[ word for word in tokens if len(word) >= 3 ] for tokens in texts]


In [16]:
# A list of extra stopwords specific to the debates transcripts (if you want to remove more stopwords)
extra_stopwords = ['will', 'people', 'need', 'think', 'well','going', 'can', 'country', 'know', 'lot', 'get','make','way','president', 'want',
                'like','say','got','said','just','something','tell','put','now', 'bad','back','want','right','every','one','use','come','never', 
                'many','along','things','day','also','first','guy', 'great', 'take', 'good', 'much','anderson', 'let', 'would', 'year', 'thing', 'america',
                'talk', 'talking', 'thank', 'does', 'give', 'look', 'believe', 'tonight','today','see']

extra_stoplist = extra_stopwords
texts = [[word for word in text if word not in extra_stoplist] for text in texts]
#https://github.com/alexperrier/datatalks/blob/master/debates/R/stm.R

### Section 2.2: Saving the dictionary for future use

In [17]:
# this is text processing required for topic modeling with Gensim

## Create a dictionary representation of the documents.
dictionary = Dictionary(texts)
dictionary.save('data/fakenews.dict')  # store the dictionary, for future reference

len(dictionary)

2018-10-28 12:57:49,382 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2018-10-28 12:57:51,529 : INFO : adding document #10000 to Dictionary(79425 unique tokens: [u'fawn', u'belligerence', u'nallen', u'cmissile', u'fdcf']...)
2018-10-28 12:57:53,257 : INFO : built Dictionary(113952 unique tokens: [u'fawn', u'dsroka', u'unsupportable', u'nallen', u'cmissile']...) from 17949 documents (total 3269562 corpus positions)
2018-10-28 12:57:53,260 : INFO : saving Dictionary object under data/fakenews.dict, separately None
2018-10-28 12:57:53,358 : INFO : saved data/fakenews.dict


113952

### Section 2.3: Removing rare words and common tokens in the dictionary

In [18]:
## Remove rare and common tokens.
# ignore words that appear in less than 5 documents or more than 50% documents (remove too frequent & infrequent words) - an optional step
dictionary.filter_extremes(no_below=5, no_above=0.5) #https://radimrehurek.com/gensim/corpora/dictionary.html#gensim.corpora.dictionary.Dictionary.filter_extremes
len(dictionary)

2018-10-28 12:58:05,867 : INFO : discarding 85252 tokens: [(u'ord', 3), (u'uuid', 1), (u'deflects', 4), (u'corroborated', 4), (u'ntargets', 1), (u'kayla', 3), (u'berserk', 4), (u'bezerk', 1), (u'cescapades', 1), (u'crally', 2)]...
2018-10-28 12:58:05,869 : INFO : keeping 28700 tokens which were in no less than 5 and no more than 8974 (=50.0%) documents
2018-10-28 12:58:05,940 : INFO : resulting dictionary: Dictionary(28700 unique tokens: [u'nallen', u'sowell', u'hanging', u'woody', u'localized']...)


28700

### Section 2.4: Saving the corpus

In [19]:
# convert words to vetors or integers
corpus = [dictionary.doc2bow(text) for text in texts]
corpora.MmCorpus.serialize('data/fakenews.mm', corpus)  # store to disk, for later use  # store to disk, for later use
len(corpus)

2018-10-28 12:58:30,456 : INFO : storing corpus in Matrix Market format to data/fakenews.mm
2018-10-28 12:58:30,460 : INFO : saving sparse matrix to data/fakenews.mm
2018-10-28 12:58:30,461 : INFO : PROGRESS: saving document #0
2018-10-28 12:58:30,986 : INFO : PROGRESS: saving document #1000
2018-10-28 12:58:31,986 : INFO : PROGRESS: saving document #2000
2018-10-28 12:58:32,529 : INFO : PROGRESS: saving document #3000
2018-10-28 12:58:32,549 : INFO : PROGRESS: saving document #4000
2018-10-28 12:58:32,553 : INFO : PROGRESS: saving document #5000
2018-10-28 12:58:32,558 : INFO : PROGRESS: saving document #6000
2018-10-28 12:58:32,562 : INFO : PROGRESS: saving document #7000
2018-10-28 12:58:32,746 : INFO : PROGRESS: saving document #8000
2018-10-28 12:58:33,404 : INFO : PROGRESS: saving document #9000
2018-10-28 12:58:34,125 : INFO : PROGRESS: saving document #10000
2018-10-28 12:58:34,342 : INFO : PROGRESS: saving document #11000
2018-10-28 12:58:34,424 : INFO : PROGRESS: saving docum

17949

In [20]:
print('Number of unique tokens: %d' % len(dictionary))
print('Number of documents: %d' % len(corpus))

Number of unique tokens: 28700
Number of documents: 17949


In [21]:
# later you can retrive the saved dict and corpus
# https://radimrehurek.com/gensim/tut1.html

saved_dict = dictionary.load('data/fakenews.dict')

#for i in saved_dict.token2id.iteritems():
#    print i

2018-10-28 12:59:16,724 : INFO : loading Dictionary object from data/fakenews.dict
2018-10-28 12:59:16,788 : INFO : loaded data/fakenews.dict


In [22]:
# you can retrieve the saved corpus

corpus_saved = corpora.MmCorpus('data/fakenews.mm')


2018-10-28 12:59:17,691 : INFO : loaded corpus index from data/fakenews.mm.index
2018-10-28 12:59:17,694 : INFO : initializing cython corpus reader from data/fakenews.mm
2018-10-28 12:59:17,696 : INFO : accepted corpus with 17949 documents, 28700 features, 1880700 non-zero entries


## Section 3: Explaining Probabilistic Topic Modeling

### Section 3.1: Explaining the difference between text classification and topic modeling

- The main difference between text classification and probabilistic topic modeling is that one is supervised machine learning, the other is unsupervised machine learning. 

- Text classification is supervised, and the goal there is to attempt to correctly classify and predict the category that a certain text should belong to, i.e. spam/not spam, political news/HR news, etc. In Text classification, we already have predefined labels and we are trying to parse our data and correctly assign each word, sentence, or document to the category that most accurately describes it.

- Probabilistic topic modeling is different. Here, we have no labels that are already given to us, we are instead trying to sift through the texts to discover certain categories or topics that exist in our texts. We are trying to discover the structure of our documents, and assign probabilities to each text that tell us how likely it is to belong to each topic that we have discovered.

### Section 3.2: Explaining the goal of LDA:

- The goal of LDA is to determine the probability that each token or sentence or document belongs to each of the n topics that we have discovered that exist in our corpus.

### Section 3.3: Explaining the document-topic matrix:

- The document topic matrix returns for every document, tuples that contain the index number of a topic indentified by our model, and the probability that that specific document belongs to that topic. ex an output of (0, .92), (1, .08) would mean that for that document, the probability that it belongs to topic 0 is 92%, and the probability that it belongs to topic 1 is 8%.

### Section 3.4: Explaining the term-topic matrix:

- The topic term matrix shows us which words are most influential for the model in determining what words define a certain topic. The output of the term topic matrix has coefficients ranging from zero to one attached to a word, and that shows us the relative importance of that word in that topic. It tells us that if we see that word in a certain document, it is a decent indication of the topic of that document.

## Section 4: Building the LDA model

### Section 4.1: LDA Model Building

In [23]:
numpy.random.seed(1) # setting random seed to get the same results each time. 
model = ldamodel.LdaModel(corpus, id2word=dictionary, num_topics=35, passes=50, eval_every = 1)

2018-10-28 13:37:01,157 : INFO : using symmetric alpha at 0.0285714285714
2018-10-28 13:37:01,161 : INFO : using symmetric eta at 0.0285714285714
2018-10-28 13:37:01,171 : INFO : using serial LDA version on this node
2018-10-28 13:37:01,562 : INFO : running online (multi-pass) LDA training, 35 topics, 50 passes over the supplied corpus of 17949 documents, updating model once every 2000 documents, evaluating perplexity every 2000 documents, iterating 50x with a convergence threshold of 0.001000
2018-10-28 13:37:04,964 : INFO : -11.377 per-word bound, 2659.9 perplexity estimate based on a held-out corpus of 2000 documents with 585900 words
2018-10-28 13:37:04,967 : INFO : PROGRESS: pass 0, at document #2000/17949
2018-10-28 13:37:06,904 : INFO : merging changes from 2000 documents into a model of 17949 documents
2018-10-28 13:37:07,055 : INFO : topic #5 (0.029): 0.007*"com" + 0.007*"trump" + 0.005*"state" + 0.005*"clinton" + 0.004*"english" + 0.004*"american" + 0.004*"nthe" + 0.004*"http

2018-10-28 13:37:21,229 : INFO : topic #30 (0.029): 0.010*"com" + 0.009*"god" + 0.008*"time" + 0.007*"silver" + 0.006*"life" + 0.006*"english" + 0.006*"world" + 0.005*"http" + 0.004*"www" + 0.004*"video"
2018-10-28 13:37:21,232 : INFO : topic #1 (0.029): 0.454*"xbc" + 0.004*"clinton" + 0.003*"trump" + 0.003*"state" + 0.003*"hillary" + 0.003*"corps" + 0.002*"burt" + 0.002*"alzheimer" + 0.002*"lynch" + 0.002*"nthe"
2018-10-28 13:37:21,234 : INFO : topic #27 (0.029): 0.474*"xba" + 0.239*"xbb" + 0.007*"xad" + 0.005*"que" + 0.004*"com" + 0.003*"http" + 0.002*"los" + 0.002*"del" + 0.002*"jpg" + 0.001*"para"
2018-10-28 13:37:21,236 : INFO : topic #24 (0.029): 0.016*"food" + 0.008*"com" + 0.005*"india" + 0.005*"english" + 0.005*"new" + 0.004*"water" + 0.004*"time" + 0.004*"soil" + 0.003*"thecommonsenseshow" + 0.003*"nthe"
2018-10-28 13:37:21,240 : INFO : topic diff=1.806112, rho=0.408248
2018-10-28 13:37:23,244 : INFO : -9.197 per-word bound, 586.9 perplexity estimate based on a held-out corpu

2018-10-28 13:37:42,441 : INFO : PROGRESS: pass 1, at document #6000/17949
2018-10-28 13:37:42,680 : INFO : merging changes from 2000 documents into a model of 17949 documents
2018-10-28 13:37:42,894 : INFO : topic #14 (0.029): 0.006*"world" + 0.006*"american" + 0.005*"nthe" + 0.005*"power" + 0.004*"war" + 0.004*"even" + 0.004*"political" + 0.004*"state" + 0.004*"new" + 0.004*"time"
2018-10-28 13:37:42,895 : INFO : topic #9 (0.029): 0.032*"clinton" + 0.030*"email" + 0.025*"fbi" + 0.020*"hillary" + 0.015*"com" + 0.014*"investigation" + 0.010*"comey" + 0.009*"new" + 0.008*"news" + 0.007*"english"
2018-10-28 13:37:42,898 : INFO : topic #25 (0.029): 0.029*"mosul" + 0.022*"isi" + 0.017*"city" + 0.016*"iraqi" + 0.008*"com" + 0.007*"force" + 0.007*"iraq" + 0.006*"kurdish" + 0.005*"marijuana" + 0.005*"english"
2018-10-28 13:37:42,901 : INFO : topic #12 (0.029): 0.008*"bank" + 0.006*"money" + 0.006*"million" + 0.005*"government" + 0.005*"billion" + 0.005*"dollar" + 0.004*"financial" + 0.004*"nt

2018-10-28 13:38:01,016 : INFO : topic #18 (0.029): 0.046*"die" + 0.032*"der" + 0.022*"und" + 0.017*"unz" + 0.014*"von" + 0.013*"den" + 0.010*"mit" + 0.009*"german" + 0.009*"sich" + 0.008*"com"
2018-10-28 13:38:01,020 : INFO : topic diff=0.710220, rho=0.316228
2018-10-28 13:38:03,877 : INFO : -7.864 per-word bound, 233.0 perplexity estimate based on a held-out corpus of 1949 documents with 500495 words
2018-10-28 13:38:03,878 : INFO : PROGRESS: pass 1, at document #17949/17949
2018-10-28 13:38:05,394 : INFO : merging changes from 1949 documents into a model of 17949 documents
2018-10-28 13:38:05,542 : INFO : topic #14 (0.029): 0.007*"world" + 0.006*"american" + 0.005*"power" + 0.005*"even" + 0.004*"nthe" + 0.004*"political" + 0.004*"state" + 0.004*"time" + 0.004*"war" + 0.004*"government"
2018-10-28 13:38:05,543 : INFO : topic #21 (0.029): 0.033*"election" + 0.031*"vote" + 0.023*"trump" + 0.021*"voter" + 0.016*"voting" + 0.015*"state" + 0.012*"hillary" + 0.011*"poll" + 0.010*"republica

2018-10-28 13:38:23,003 : INFO : topic #17 (0.029): 0.047*"police" + 0.024*"officer" + 0.022*"protester" + 0.012*"shot" + 0.011*"gun" + 0.011*"cop" + 0.010*"sheriff" + 0.009*"camp" + 0.009*"fire" + 0.008*"enforcement"
2018-10-28 13:38:23,006 : INFO : topic #8 (0.029): 0.015*"russia" + 0.015*"state" + 0.015*"china" + 0.010*"european" + 0.010*"europe" + 0.010*"world" + 0.008*"international" + 0.007*"africa" + 0.006*"south" + 0.006*"global"
2018-10-28 13:38:23,009 : INFO : topic #0 (0.029): 0.006*"medium" + 0.005*"state" + 0.005*"american" + 0.004*"policy" + 0.004*"time" + 0.003*"issue" + 0.003*"even" + 0.003*"nthe" + 0.003*"company" + 0.003*"internet"
2018-10-28 13:38:23,013 : INFO : topic diff=0.600867, rho=0.301511
2018-10-28 13:38:24,440 : INFO : -8.850 per-word bound, 461.5 perplexity estimate based on a held-out corpus of 2000 documents with 124657 words
2018-10-28 13:38:24,443 : INFO : PROGRESS: pass 2, at document #12000/17949
2018-10-28 13:38:25,298 : INFO : merging changes from 

...

2018-10-28 14:05:31,704 : INFO : topic #22 (0.029): 0.033*"law" + 0.022*"state" + 0.020*"government" + 0.017*"court" + 0.015*"federal" + 0.012*"case" + 0.011*"crime" + 0.011*"school" + 0.010*"student" + 0.010*"justice"
2018-10-28 14:05:31,707 : INFO : topic #16 (0.029): 0.137*"trump" + 0.032*"donald" + 0.018*"election" + 0.016*"hillary" + 0.013*"american" + 0.012*"clinton" + 0.011*"white" + 0.009*"win" + 0.009*"supporter" + 0.008*"medium"
2018-10-28 14:05:31,710 : INFO : topic #33 (0.029): 0.053*"nuclear" + 0.048*"veteran" + 0.023*"weapon" + 0.022*"north" + 0.020*"korea" + 0.014*"ban" + 0.013*"post" + 0.012*"south" + 0.011*"flag" + 0.011*"korean"
2018-10-28 14:05:31,713 : INFO : topic #8 (0.029): 0.016*"china" + 0.016*"state" + 0.011*"european" + 0.010*"jew" + 0.010*"jewish" + 0.010*"europe" + 0.010*"world" + 0.009*"international" + 0.009*"united" + 0.008*"african"
2018-10-28 14:05:31,719 : INFO : topic diff=0.077614, rho=0.133631
2018-10-28 14:05:32,013 : INFO : -133.171 per-word boun

2018-10-28 14:05:46,809 : INFO : topic diff=0.064119, rho=0.133631
2018-10-28 14:05:50,308 : INFO : -8.316 per-word bound, 318.7 perplexity estimate based on a held-out corpus of 2000 documents with 530416 words
2018-10-28 14:05:50,309 : INFO : PROGRESS: pass 47, at document #16000/17949
2018-10-28 14:05:52,447 : INFO : merging changes from 2000 documents into a model of 17949 documents
2018-10-28 14:05:52,595 : INFO : topic #10 (0.029): 0.021*"soros" + 0.015*"general" + 0.011*"retired" + 0.010*"source" + 0.007*"nsa" + 0.007*"time" + 0.006*"state" + 0.006*"george" + 0.006*"note" + 0.005*"goldman"
2018-10-28 14:05:52,598 : INFO : topic #29 (0.029): 0.051*"com" + 0.026*"video" + 0.026*"http" + 0.024*"woman" + 0.020*"english" + 0.019*"october" + 0.019*"jpg" + 0.019*"twitter" + 0.018*"uploads" + 0.017*"content"
2018-10-28 14:05:52,598 : INFO : topic #12 (0.029): 0.013*"money" + 0.012*"bank" + 0.010*"market" + 0.009*"gold" + 0.008*"economy" + 0.008*"dollar" + 0.008*"government" + 0.008*"mil

2018-10-28 14:06:09,559 : INFO : topic #32 (0.029): 0.149*"xce" + 0.075*"xcf" + 0.037*"black" + 0.010*"city" + 0.008*"white" + 0.008*"immigrant" + 0.007*"border" + 0.006*"mexico" + 0.004*"xac" + 0.003*"mexican"
2018-10-28 14:06:09,561 : INFO : topic #26 (0.029): 0.014*"health" + 0.013*"study" + 0.008*"cancer" + 0.008*"body" + 0.008*"drug" + 0.006*"found" + 0.006*"medical" + 0.006*"research" + 0.006*"effect" + 0.005*"child"
2018-10-28 14:06:09,565 : INFO : topic diff=0.137723, rho=0.132453
2018-10-28 14:06:13,984 : INFO : -8.193 per-word bound, 292.7 perplexity estimate based on a held-out corpus of 2000 documents with 659670 words
2018-10-28 14:06:13,986 : INFO : PROGRESS: pass 48, at document #10000/17949
2018-10-28 14:06:16,677 : INFO : merging changes from 2000 documents into a model of 17949 documents
2018-10-28 14:06:16,825 : INFO : topic #16 (0.029): 0.140*"trump" + 0.032*"donald" + 0.019*"election" + 0.016*"hillary" + 0.013*"american" + 0.012*"clinton" + 0.010*"white" + 0.010*"w

2018-10-28 14:06:39,953 : INFO : topic #11 (0.029): 0.016*"campaign" + 0.006*"former" + 0.006*"clinton" + 0.005*"public" + 0.005*"nthe" + 0.005*"house" + 0.005*"national" + 0.005*"democratic" + 0.004*"john" + 0.004*"podesta"
2018-10-28 14:06:39,956 : INFO : topic #12 (0.029): 0.012*"money" + 0.012*"bank" + 0.009*"market" + 0.009*"million" + 0.008*"dollar" + 0.008*"economy" + 0.008*"government" + 0.008*"gold" + 0.007*"financial" + 0.006*"percent"
2018-10-28 14:06:39,959 : INFO : topic #19 (0.029): 0.101*"com" + 0.071*"http" + 0.048*"xaf" + 0.047*"english" + 0.042*"jpg" + 0.039*"www" + 0.027*"org" + 0.025*"content" + 0.022*"uploads" + 0.020*"israel"
2018-10-28 14:06:39,961 : INFO : topic #34 (0.029): 0.200*"clinton" + 0.112*"hillary" + 0.035*"foundation" + 0.028*"bill" + 0.018*"million" + 0.013*"wikileaks" + 0.011*"email" + 0.009*"money" + 0.007*"haiti" + 0.007*"com"
2018-10-28 14:06:39,966 : INFO : topic diff=0.091417, rho=0.131306
2018-10-28 14:06:41,927 : INFO : -8.221 per-word bound,

2018-10-28 14:06:54,838 : INFO : topic diff=0.091986, rho=0.131306
2018-10-28 14:06:56,914 : INFO : -8.470 per-word bound, 354.6 perplexity estimate based on a held-out corpus of 2000 documents with 282716 words
2018-10-28 14:06:56,917 : INFO : PROGRESS: pass 49, at document #14000/17949
2018-10-28 14:06:58,194 : INFO : merging changes from 2000 documents into a model of 17949 documents
2018-10-28 14:06:58,351 : INFO : topic #24 (0.029): 0.032*"food" + 0.019*"water" + 0.010*"plant" + 0.007*"best" + 0.006*"store" + 0.006*"eat" + 0.005*"may" + 0.005*"home" + 0.005*"survival" + 0.005*"help"
2018-10-28 14:06:58,352 : INFO : topic #18 (0.029): 0.052*"der" + 0.047*"die" + 0.028*"und" + 0.018*"den" + 0.017*"von" + 0.014*"mit" + 0.012*"com" + 0.012*"sich" + 0.011*"dem" + 0.011*"xbcr"
2018-10-28 14:06:58,354 : INFO : topic #34 (0.029): 0.193*"clinton" + 0.108*"hillary" + 0.032*"foundation" + 0.028*"bill" + 0.017*"million" + 0.012*"wikileaks" + 0.010*"email" + 0.009*"money" + 0.008*"dave" + 0.00

### Section 4.2: Saving the model for future use

In [24]:
model.save('data/fakenewslda.model') # same for tfidf, lda, ...
#model = models.LdaModel.load('data/lda.model') how to retrieve the model so we dont have to rebuilt it every time

#https://stackoverflow.com/questions/17354417/gensim-how-to-save-lda-models-produced-topics-to-a-readable-format-csv-txt-et

2018-10-28 14:15:51,349 : INFO : saving LdaState object under data/fakenewslda.model.state, separately None
2018-10-28 14:15:51,357 : INFO : saved data/fakenewslda.model.state
2018-10-28 14:15:51,430 : INFO : saving LdaModel object under data/fakenewslda.model, separately ['expElogbeta', 'sstats']
2018-10-28 14:15:51,433 : INFO : not storing attribute id2word
2018-10-28 14:15:51,434 : INFO : storing np array 'expElogbeta' to data/fakenewslda.model.expElogbeta.npy
2018-10-28 14:15:51,440 : INFO : not storing attribute state
2018-10-28 14:15:51,441 : INFO : not storing attribute dispatcher
2018-10-28 14:15:51,447 : INFO : saved data/fakenewslda.model


### Section 4.3: Printing the topics.

In [25]:
model.show_topics(num_topics=35)
#show_topics(num_topics=10, num_words=10, log=False, formatted=True)

[(0,
  u'0.013*"comment" + 0.013*"medium" + 0.013*"text" + 0.011*"result" + 0.011*"news" + 0.009*"post" + 0.009*"name" + 0.007*"com" + 0.006*"website" + 0.006*"article"'),
 (1,
  u'0.838*"xbc" + 0.009*"preview" + 0.007*"modi" + 0.005*"theunrealtimes" + 0.004*"singh" + 0.003*"gerardo" + 0.003*"kejriwal" + 0.003*"rupee" + 0.003*"aap" + 0.002*"burt"'),
 (2,
  u'0.039*"war" + 0.019*"syria" + 0.013*"state" + 0.012*"government" + 0.010*"saudi" + 0.010*"policy" + 0.010*"iran" + 0.010*"foreign" + 0.009*"russia" + 0.009*"military"'),
 (3,
  u'0.052*"que" + 0.034*"xaa" + 0.032*"del" + 0.025*"los" + 0.019*"por" + 0.016*"con" + 0.015*"para" + 0.014*"xada" + 0.013*"una" + 0.011*"xac"'),
 (4,
  u'0.015*"usa" + 0.014*"british" + 0.013*"brexit" + 0.012*"migrant" + 0.012*"refugee" + 0.011*"english" + 0.011*"britain" + 0.010*"http" + 0.009*"may" + 0.009*"party"'),
 (5,
  u'0.010*"energy" + 0.009*"new" + 0.008*"earth" + 0.008*"light" + 0.007*"world" + 0.006*"planet" + 0.006*"system" + 0.006*"space" + 0.0

In [26]:
# Prints the topics.
for top in model.show_topics(num_topics=35):
    print top

(0, u'0.013*"comment" + 0.013*"medium" + 0.013*"text" + 0.011*"result" + 0.011*"news" + 0.009*"post" + 0.009*"name" + 0.007*"com" + 0.006*"website" + 0.006*"article"')
(1, u'0.838*"xbc" + 0.009*"preview" + 0.007*"modi" + 0.005*"theunrealtimes" + 0.004*"singh" + 0.003*"gerardo" + 0.003*"kejriwal" + 0.003*"rupee" + 0.003*"aap" + 0.002*"burt"')
(2, u'0.039*"war" + 0.019*"syria" + 0.013*"state" + 0.012*"government" + 0.010*"saudi" + 0.010*"policy" + 0.010*"iran" + 0.010*"foreign" + 0.009*"russia" + 0.009*"military"')
(3, u'0.052*"que" + 0.034*"xaa" + 0.032*"del" + 0.025*"los" + 0.019*"por" + 0.016*"con" + 0.015*"para" + 0.014*"xada" + 0.013*"una" + 0.011*"xac"')
(4, u'0.015*"usa" + 0.014*"british" + 0.013*"brexit" + 0.012*"migrant" + 0.012*"refugee" + 0.011*"english" + 0.011*"britain" + 0.010*"http" + 0.009*"may" + 0.009*"party"')
(5, u'0.010*"energy" + 0.009*"new" + 0.008*"earth" + 0.008*"light" + 0.007*"world" + 0.006*"planet" + 0.006*"system" + 0.006*"space" + 0.006*"time" + 0.006*"coul

In [27]:
# print words without probability
for i in range(0,35):
    topics = model.show_topic(i, 10)
    print ', '.join([str(word[0]) for word in topics])

comment, medium, text, result, news, post, name, com, website, article
xbc, preview, modi, theunrealtimes, singh, gerardo, kejriwal, rupee, aap, burt
war, syria, state, government, saudi, policy, iran, foreign, russia, military
que, xaa, del, los, por, con, para, xada, una, xac
usa, british, brexit, migrant, refugee, english, britain, http, may, party
energy, new, earth, light, world, planet, system, space, time, could
obama, house, white, nobama, american, new, administration, obamacare, state, party
california, assange, onion, source, wikileaks, julian, state, john, nation, spam
china, state, european, europe, world, international, united, jew, new, india
clinton, email, fbi, hillary, investigation, comey, server, new, information, weiner
soros, general, retired, source, nsa, time, state, george, note, goldman
campaign, former, public, clinton, nthe, house, national, john, york, podesta
money, bank, market, gold, dollar, government, economy, million, financial, tax
est, admin, wmw, v

### Section 4.4: Assigning the topics to the documents in corpus

In [28]:
lda_corpus = model[corpus]

results = []
for i in lda_corpus:
    print i
    results.append(i)
print 

[(0, 0.6772955), (7, 0.03108106), (9, 0.06534063), (13, 0.045441408), (31, 0.14787437)]
[(1, 0.0151260495), (6, 0.052293655), (12, 0.27835983), (22, 0.14718264), (25, 0.13377754), (28, 0.020799652), (29, 0.21831024), (32, 0.12280582)]
[(1, 0.08563912), (2, 0.073123164), (9, 0.25528973), (10, 0.08551432), (11, 0.35073698), (14, 0.06303932), (29, 0.06477764)]
[(0, 0.04014129), (6, 0.023294114), (8, 0.028659314), (9, 0.6471951), (22, 0.0148728), (28, 0.032766555), (29, 0.12906697), (30, 0.071529)]
[(6, 0.18584684), (14, 0.08139998), (16, 0.17914423), (20, 0.031745173), (25, 0.09503545), (29, 0.22371338), (30, 0.14365673), (31, 0.016154693), (32, 0.03169643)]
[(0, 0.026560664), (6, 0.14838094), (9, 0.020744573), (11, 0.038177077), (12, 0.37032774), (14, 0.06285884), (16, 0.036360484), (19, 0.035968296), (21, 0.058204647), (22, 0.07984), (24, 0.037100565), (26, 0.051746495), (32, 0.021494739)]
[(6, 0.022293748), (16, 0.09336623), (17, 0.055064313), (21, 0.07395154), (28, 0.017595856), (29, 

[(0, 0.052692845), (2, 0.013502819), (5, 0.026238585), (6, 0.011367496), (7, 0.0412812), (9, 0.107507415), (10, 0.016240181), (11, 0.020440856), (12, 0.015517899), (14, 0.16961569), (16, 0.106078036), (17, 0.032911453), (21, 0.04505607), (22, 0.034004875), (26, 0.0299457), (29, 0.010336417), (30, 0.19820014), (32, 0.04099652), (34, 0.013377363)]
[(0, 0.031901825), (8, 0.09986163), (9, 0.03809974), (10, 0.051941007), (11, 0.037659995), (12, 0.08734087), (14, 0.24468134), (16, 0.25046846), (19, 0.0483927), (34, 0.10321744)]
[(0, 0.018893706), (9, 0.7818634), (11, 0.116652444), (14, 0.034324303), (21, 0.02183292), (34, 0.015646083)]
[(9, 0.69944394), (12, 0.051368464), (14, 0.028065216), (16, 0.03201458), (30, 0.17432947)]
[(0, 0.16128315), (6, 0.08052774), (9, 0.46097192), (19, 0.22111338), (33, 0.041818127)]
[(0, 0.05828746), (9, 0.5316915), (12, 0.042360634), (16, 0.097833574), (30, 0.19530198), (32, 0.059728887)]
[(0, 0.39177522), (9, 0.08204712), (10, 0.13440725), (19, 0.30025876), (

[(0, 0.18041104), (9, 0.06722276), (11, 0.21594726), (13, 0.077728584), (19, 0.08018092), (23, 0.08003554), (29, 0.15514654), (32, 0.09137214), (33, 0.030730704)]
[(2, 0.37949014), (19, 0.11363933), (23, 0.066203155), (28, 0.3672984), (29, 0.051391)]
[(17, 0.6845793), (19, 0.046092752), (23, 0.18778825), (33, 0.06045124)]
[(22, 0.025295386), (23, 0.6627228), (29, 0.109025136), (32, 0.18488085)]
[(10, 0.040055834), (12, 0.14486554), (13, 0.04486597), (19, 0.093173124), (21, 0.2041061), (23, 0.111063026), (26, 0.338341)]
[(0, 0.15440416), (5, 0.055895537), (6, 0.013108316), (9, 0.024181694), (11, 0.03548713), (12, 0.046617664), (13, 0.013480591), (14, 0.30111927), (16, 0.029468333), (21, 0.011413125), (23, 0.024368806), (24, 0.024775852), (26, 0.05806468), (28, 0.01517302), (29, 0.043047346), (30, 0.09750634), (32, 0.02118177), (34, 0.016121514)]
[(0, 0.043905694), (10, 0.061719976), (19, 0.13953821), (22, 0.0366456), (23, 0.6950245)]
[(5, 0.10203094), (8, 0.22283669), (11, 0.13705753), 

[(0, 0.020842453), (2, 0.14480458), (4, 0.012828348), (5, 0.017694252), (6, 0.0127740875), (7, 0.109327585), (9, 0.05771821), (11, 0.19470403), (12, 0.016458888), (14, 0.17589311), (16, 0.029540379), (22, 0.07874393), (28, 0.04561086), (30, 0.028265098), (34, 0.033243276)]
[(0, 0.020342568), (2, 0.03229214), (6, 0.12271819), (11, 0.022612764), (12, 0.20835753), (14, 0.19419354), (21, 0.052361246), (22, 0.2574067), (25, 0.01046933), (26, 0.038059946), (32, 0.019119652)]
[(12, 0.1299379), (19, 0.5191548), (22, 0.07534552), (26, 0.18340299), (33, 0.05919178)]
[(0, 0.09573386), (8, 0.21397617), (9, 0.028343486), (11, 0.03413082), (12, 0.0119595), (13, 0.035597447), (14, 0.32216817), (17, 0.030543972), (22, 0.08770471), (25, 0.010472975), (26, 0.05544761), (28, 0.022789167), (29, 0.040247794)]
[(2, 0.03848481), (4, 0.01804337), (6, 0.04574023), (8, 0.012089704), (10, 0.011102457), (11, 0.02421893), (12, 0.05065818), (14, 0.4705975), (16, 0.2025459), (21, 0.03309215), (30, 0.061519094)]
[(0,

[(0, 0.026375795), (6, 0.12677571), (8, 0.013070813), (11, 0.0228313), (12, 0.07495228), (14, 0.21113977), (16, 0.07814395), (21, 0.037903775), (26, 0.02642895), (29, 0.052867062), (30, 0.22147688), (32, 0.08456192), (33, 0.013390537)]
[(0, 0.2037184), (13, 0.13549891), (16, 0.14622092), (29, 0.3380862), (31, 0.05350761), (32, 0.078182034), (33, 0.032478247)]
[(0, 0.07763652), (2, 0.039989114), (4, 0.018645713), (5, 0.027384313), (6, 0.014381933), (8, 0.07058614), (11, 0.038433053), (12, 0.016018884), (14, 0.35113466), (16, 0.15637037), (17, 0.011569866), (22, 0.01456297), (24, 0.010488777), (25, 0.02569865), (29, 0.039453212), (30, 0.036310382), (32, 0.03001786)]
[(5, 0.04171386), (12, 0.06506885), (14, 0.16498382), (16, 0.3410683), (29, 0.24890944), (31, 0.12607087)]
[(0, 0.028388238), (6, 0.1561278), (8, 0.013450808), (14, 0.3674203), (16, 0.15679467), (21, 0.04760282), (22, 0.102770954), (29, 0.04531368), (30, 0.028855477), (32, 0.043278966)]
[(0, 0.041889586), (4, 0.04627267), (6,

...

[(5, 0.038676966), (7, 0.07198188), (9, 0.12711936), (11, 0.37402692), (19, 0.36502886)]
[(0, 0.027738033), (11, 0.118928865), (13, 0.012500232), (14, 0.09208384), (16, 0.03539062), (17, 0.02780645), (19, 0.018158752), (21, 0.026072258), (22, 0.09147946), (29, 0.18338726), (30, 0.32243234), (33, 0.011626184)]
[(9, 0.03963025), (16, 0.47668526), (19, 0.38500533), (21, 0.034533735), (34, 0.03557397)]
[(7, 0.03526828), (17, 0.14549667), (19, 0.3932327), (21, 0.040926285), (22, 0.19903535), (29, 0.122503616), (32, 0.035950873)]
[(13, 0.044426493), (17, 0.06902573), (19, 0.3554993), (21, 0.036599994), (22, 0.28038958), (29, 0.11619338), (32, 0.07027934)]
[(9, 0.18169527), (11, 0.03573811), (12, 0.0425919), (16, 0.102797806), (17, 0.067440905), (19, 0.120668136), (21, 0.020584606), (22, 0.26247644), (24, 0.020559413), (30, 0.0711766), (32, 0.0661075)]
[(12, 0.08170672), (17, 0.050584435), (19, 0.42884082), (21, 0.040881082), (22, 0.25899985), (23, 0.040459506), (29, 0.06775837)]
[(6, 0.08832

[(0, 0.13290694), (5, 0.19616334), (9, 0.014628889), (10, 0.090213105), (11, 0.14743328), (12, 0.097582236), (14, 0.12698235), (21, 0.14569566), (26, 0.011912093), (32, 0.013113219)]
[(9, 0.011111652), (31, 0.94542766)]
[(0, 0.10219903), (5, 0.08385433), (6, 0.08710267), (9, 0.293055), (10, 0.015795134), (11, 0.16084248), (14, 0.029142084), (16, 0.014696066), (19, 0.10595048), (24, 0.010883545), (26, 0.012404181), (30, 0.066144004)]
[(31, 0.94670916)]
[(31, 0.94827455)]
[(29, 0.011881252), (30, 0.015120873), (31, 0.92108214)]
[(0, 0.063972004), (4, 0.013770319), (5, 0.010879146), (6, 0.020670915), (7, 0.075260274), (10, 0.04435666), (11, 0.29678848), (14, 0.30622068), (21, 0.110265695), (26, 0.012980442), (34, 0.026976602)]
[(0, 0.04308368), (5, 0.047105465), (9, 0.029525956), (10, 0.017334413), (14, 0.08105047), (22, 0.016022393), (24, 0.041729715), (29, 0.025931358), (30, 0.022354107), (31, 0.6330248)]
[(0, 0.092343494), (6, 0.09562172), (8, 0.08473529), (9, 0.027737103), (11, 0.0776

[(0, 0.060405754), (5, 0.3440926), (11, 0.010238202), (13, 0.026358934), (14, 0.11807423), (18, 0.016127277), (21, 0.025812915), (22, 0.011465622), (23, 0.021660978), (26, 0.15633936), (30, 0.17614028), (32, 0.020042755)]
[(0, 0.034361385), (5, 0.4170816), (8, 0.021325322), (14, 0.19391908), (16, 0.02879011), (17, 0.08293448), (25, 0.027568534), (26, 0.03983043), (29, 0.09521817), (30, 0.042088035), (33, 0.0111685945)]
[(0, 0.022534154), (2, 0.05616919), (5, 0.031179467), (8, 0.06546291), (11, 0.1832012), (14, 0.11126824), (16, 0.057170548), (19, 0.019632919), (21, 0.09650772), (23, 0.030047426), (33, 0.2686243), (34, 0.048988674)]
[(0, 0.08035987), (5, 0.012531538), (9, 0.026741495), (10, 0.0208592), (11, 0.066032246), (13, 0.013132261), (14, 0.06646005), (16, 0.010713619), (17, 0.20717269), (23, 0.38198864), (26, 0.013653456), (29, 0.08019137), (32, 0.014666187)]
[(0, 0.055822574), (4, 0.011130428), (6, 0.025017865), (9, 0.066665724), (10, 0.059184298), (11, 0.31001484), (12, 0.01263

[(0, 0.020102583), (4, 0.01643542), (9, 0.7923066), (11, 0.061114505), (16, 0.06902755), (21, 0.013237739), (24, 0.010715771)]
[(0, 0.02563819), (8, 0.011740702), (9, 0.01531668), (10, 0.018882012), (12, 0.013319299), (13, 0.018164366), (14, 0.09634707), (17, 0.07095527), (22, 0.09139134), (24, 0.16692957), (26, 0.08375022), (29, 0.042648446), (30, 0.29161382), (32, 0.03561021)]
[(0, 0.038664088), (2, 0.1874842), (5, 0.022867106), (8, 0.15913503), (9, 0.010836514), (12, 0.024289904), (14, 0.13403997), (23, 0.018576907), (25, 0.010577855), (28, 0.33703008), (29, 0.03470076)]
[(0, 0.028786708), (4, 0.060921397), (5, 0.017400475), (8, 0.41865838), (9, 0.05255275), (13, 0.01721117), (14, 0.03133751), (17, 0.032432605), (19, 0.16691919), (21, 0.0263405), (24, 0.01263056), (27, 0.014560438), (29, 0.02389871), (30, 0.07626317)]
[(0, 0.034115992), (5, 0.01567505), (9, 0.02453576), (14, 0.119407006), (17, 0.021141566), (22, 0.025798202), (24, 0.0367643), (26, 0.5478484), (29, 0.011193435), (30,

[(9, 0.17318304), (12, 0.20162943), (21, 0.12145608), (24, 0.07965756), (28, 0.08850337), (29, 0.22470729), (30, 0.07276803)]
[(9, 0.28863966), (12, 0.4406349), (16, 0.12075127), (24, 0.055428218), (32, 0.05558493)]
[(0, 0.035657518), (5, 0.09387633), (9, 0.03720886), (11, 0.024333674), (12, 0.39712307), (14, 0.20052078), (24, 0.10419961), (26, 0.056787), (29, 0.041655246)]
[(9, 0.23430641), (12, 0.32019687), (13, 0.06717949), (16, 0.19921786), (24, 0.13148032)]
[(0, 0.13928813), (5, 0.11191646), (9, 0.078360274), (12, 0.2835294), (14, 0.20928669), (17, 0.09203473), (26, 0.05250308), (34, 0.022366911)]
[(5, 0.12764421), (9, 0.19316895), (12, 0.29076064), (13, 0.049976546), (19, 0.23604609), (32, 0.06637871)]
[(9, 0.2157641), (12, 0.37411675), (21, 0.15701805), (24, 0.10936046), (29, 0.10802639)]
[(0, 0.046193644), (9, 0.15697002), (12, 0.4717463), (14, 0.047924504), (19, 0.14949761), (24, 0.047664315), (34, 0.046670258)]
[(0, 0.06032553), (9, 0.27052045), (12, 0.25169683), (17, 0.09656

In [29]:
# finding highest value from each row
toptopic = [max(collection, key=lambda x: x[1])[0] for collection in results]
toptopic

[0,
 12,
 11,
 9,
 29,
 12,
 29,
 9,
 11,
 9,
 30,
 29,
 14,
 22,
 21,
 6,
 29,
 29,
 16,
 30,
 21,
 12,
 29,
 16,
 16,
 30,
 29,
 11,
 21,
 16,
 29,
 30,
 30,
 17,
 2,
 9,
 9,
 11,
 11,
 12,
 2,
 11,
 2,
 29,
 28,
 14,
 12,
 29,
 29,
 14,
 14,
 16,
 29,
 14,
 16,
 21,
 14,
 14,
 21,
 21,
 0,
 14,
 2,
 21,
 21,
 34,
 34,
 21,
 21,
 34,
 0,
 21,
 0,
 9,
 5,
 21,
 0,
 21,
 0,
 0,
 21,
 14,
 0,
 14,
 0,
 16,
 22,
 9,
 9,
 0,
 9,
 30,
 30,
 19,
 22,
 9,
 22,
 30,
 22,
 19,
 22,
 22,
 9,
 9,
 22,
 22,
 19,
 10,
 2,
 2,
 30,
 16,
 9,
 9,
 9,
 9,
 0,
 9,
 9,
 9,
 26,
 9,
 9,
 9,
 19,
 19,
 2,
 2,
 2,
 9,
 9,
 9,
 19,
 34,
 21,
 9,
 19,
 21,
 9,
 21,
 9,
 34,
 34,
 30,
 9,
 30,
 9,
 11,
 0,
 9,
 30,
 13,
 9,
 9,
 9,
 9,
 9,
 9,
 9,
 13,
 5,
 5,
 30,
 5,
 30,
 30,
 16,
 30,
 30,
 30,
 30,
 28,
 30,
 5,
 21,
 14,
 30,
 30,
 30,
 30,
 30,
 30,
 0,
 16,
 30,
 26,
 29,
 16,
 30,
 5,
 21,
 5,
 30,
 21,
 21,
 30,
 32,
 30,
 30,
 30,
 14,
 30,
 5,
 11,
 14,
 5,
 30,
 30,
 30,
 30,
 30,
 30,
 14,
 2,
 

In [30]:
toptopic = pd.DataFrame(toptopic)
documents = pd.DataFrame(documents)
documents = documents.rename(columns = {0: 'documents'})
summary = documents.join(toptopic)
summary.head()

documents   0
0   uuid ord in thread author published title tex...   0
1   a f bcd d b e ad f db db Barracuda Brigade T ...  12
2   bdc d ef cf f f a be d b reasoning with facts...  11
3   c e fdd de e c b de ed bc Barracuda Brigade T...   9
4   cf c ac a dd f bd ea ed Fed Up T PIN DROP SPE...  29

In [36]:
summary.groupby(0).count()

documents
0            
0        4853
1           2
2         414
3         296
4         136
5         483
6         291
7          44
8         248
9         556
10         78
11        464
12        943
13        116
14       1990
16        512
17        213
18        115
19        507
20        471
21        540
22        277
23        213
24        215
25        214
26        374
28        570
29        476
30       1992
31         59
32         86
33         96
34        105

### Section 4.5: Visualizing the results

In [32]:
import pyLDAvis.gensim

In [33]:
pyLDAvis.enable_notebook()
pyLDAvis.gensim.prepare(model, corpus, dictionary, sort_topics=False)

PreparedData(topic_coordinates=            Freq  cluster  topics         x         y
topic                                                
0       3.502184        1       1  0.017602  0.110695
1       0.514076        1       2 -0.230334 -0.068290
2       4.672415        1       3  0.159794 -0.094947
3       1.617984        1       4 -0.219948 -0.001821
4       1.177469        1       5 -0.010020  0.036889
5       3.717893        1       6  0.139654 -0.027494
6       3.183332        1       7  0.098974 -0.069849
7       0.411339        1       8 -0.130417 -0.066051
8       2.816208        1       9  0.089371 -0.136418
9       3.737928        1      10  0.146718  0.062783
10      1.294863        1      11  0.054476  0.003941
11      6.160049        1      12  0.181028 -0.001970
12      5.124454        1      13  0.149469 -0.084636
13      1.019829        1      14 -0.075455  0.043869
14     15.240100        1      15  0.184411 -0.098508
15      0.876515        1      16 -0.255270 -0.094294
16      4.034064        1      17  0.113655  0.063914
17      1.664763        1      18  0.060021  0.019621
18      0.783396        1      19 -0.214414  0.048599
19      1.093258        1      20 -0.130261  0.322572
20      3.155797        1      21 -0.261208 -0.111837
21      3.738692        1      22  0.151454  0.054330
22      2.887734        1      23  0.129496 -0.073577
23      1.674169        1      24  0.058444  0.023446
24      1.712515        1      25  0.008874 -0.002979
25      1.702680        1      26  0.063301  0.023850
26      3.411889        1      27  0.110069 -0.043509
27      0.096958        1      28 -0.219762 -0.101069
28      4.281309        1      29  0.141693 -0.044328
29      2.688574        1      30  0.001020  0.313842
30      7.518671        1      31  0.150212  0.003324
31      0.446870        1      32 -0.214750 -0.031532
32      2.098778        1      33 -0.190748 -0.049000
33      0.646701        1      34 -0.027038  0.017175
34      1.296548        1      35 -0.030114  0.053258, topic_info=      Category          Freq       Term         Total  loglift  logprob
term                                                                   
12005  Default  46904.000000        xbe  46904.000000  30.0000  30.0000
12006  Default  28831.000000        xbd  28831.000000  29.0000  29.0000
12009  Default  13348.000000        xbc  13348.000000  28.0000  28.0000
12010  Default  17699.000000        xbb  17699.000000  27.0000  27.0000
15488  Default  17901.000000    clinton  17901.000000  26.0000  26.0000
27410  Default  18376.000000      trump  18376.000000  25.0000  25.0000
12008  Default  14039.000000        xba  14039.000000  24.0000  24.0000
1435   Default  12194.000000        xce  12194.000000  23.0000  23.0000
12007  Default  12913.000000        xbf  12913.000000  22.0000  22.0000
25663  Default  11173.000000    hillary  11173.000000  21.0000  21.0000
9101   Default  15008.000000        com  15008.000000  20.0000  20.0000
1434   Default   6118.000000        xcf   6118.000000  19.0000  19.0000
5652   Default   9404.000000   election   9404.000000  18.0000  18.0000
3781   Default   7006.000000     russia   7006.000000  17.0000  17.0000
3381   Default   7531.000000       http   7531.000000  16.0000  16.0000
16371  Default   8087.000000        war   8087.000000  15.0000  15.0000
24779  Default  13232.000000      state  13232.000000  14.0000  14.0000
8151   Default   6216.000000      obama   6216.000000  13.0000  13.0000
8666   Default   6038.000000      email   6038.000000  12.0000  12.0000
10108  Default   4993.000000    russian   4993.000000  11.0000  11.0000
28570  Default   8672.000000    english   8672.000000  10.0000  10.0000
2265   Default   4359.000000        fbi   4359.000000   9.0000   9.0000
27231  Default   4441.000000     donald   4441.000000   8.0000   8.0000
7710   Default   4220.000000       vote   4220.000000   7.0000   7.0000
25653  Default   4197.000000        law   4197.000000   6.0000   6.0000
24790  Default 

### Section 4.6: Results of the topic modeling:

- The 5 most popular topics in fake news according to our model are topics 0, 12, 11, 9, and 29. Based on the words in those topics, I would say that those individual topics can be labeled as follows:

0: Discussion/Links

12: Economics

11: Hillary Clinton Presedential Campaign

9: Hillary Clinton's FBI Email Investigation

29: Russia

- So based on our model of the fake news articles, it seems like the most common topics in fake news are spam links to other pages, discussions of economics, misinformation about hillary clinton's email server and her presidential campaign, and finally Russia.

## Section 5: Applying our model to new data

In [37]:
unlabeled = ['https this is a link to another comment on a different news page',
            'we know that they are controlling the economy and the banks and big business and the government we need to invest in gold and not pay tax',
            'hillary clinton colluded with the russian government to bring about the new world order and implement agenda twenty one and make us all poor because she loves socialism',
            'hillary clinton deleted three trillion emails and she ran a pedophile sex ring from the basement of a pizza place that didnt have a basement',
            'I think that the russians are paying people in the migrant caravan to come to america and take jobs away from americans and commit a lot of crimes']

In [38]:
# Remove useless numbers and alphanumerical words
unlabeled = [re.sub("[^a-zA-Z]+", " ", text) for text in unlabeled]
# tokenize
unlabeled = [[word for word in text.lower().split() ] for text in unlabeled]
# stemming words: having --> have; friends --> friend
lmtzr = WordNetLemmatizer()
unlabeled = [[lmtzr.lemmatize(word) for word in text ] for text in unlabeled]
# remove common words 
stoplist = stopwords.words('english')
unlabeled = [[word for word in text if word not in stoplist] for text in unlabeled]
#remove short words
unlabeled = [[ word for word in tokens if len(word) >= 3 ] for tokens in unlabeled]

In [39]:
for i in unlabeled:
    print model.id2word.doc2bow(i)

[(1, 1), (21, 1), (49, 1), (235, 1), (547, 1), (785, 1), (2381, 1)]
[(47, 1), (60, 1), (306, 1), (406, 1), (1365, 1), (2093, 1), (2376, 1), (3232, 1), (3270, 1), (4740, 1)]
[(47, 1), (185, 1), (200, 1), (221, 1), (304, 1), (622, 1), (1286, 1), (1663, 1), (2129, 1), (2440, 1), (2476, 1), (4221, 1), (4597, 1), (8342, 1), (12369, 1)]
[(200, 1), (211, 1), (221, 1), (633, 1), (675, 1), (1171, 1), (1295, 1), (2039, 1), (5000, 2), (5626, 1), (6473, 1), (8111, 1), (12075, 1), (17656, 1)]
[(35, 1), (80, 1), (493, 1), (534, 1), (2272, 1), (2440, 1), (2786, 1), (3871, 1)]


In [40]:
for i in unlabeled:
    bow = model.id2word.doc2bow(i)
    doc_topics, word_topics, phi_values = model.get_document_topics(bow, per_word_topics=True)
    print doc_topics

[(0, 0.48634645), (5, 0.27511367), (19, 0.12425413)]
[(5, 0.09370782), (12, 0.82057786)]
[(10, 0.07384604), (14, 0.57333744), (28, 0.07980153), (30, 0.092661954), (34, 0.12678164)]
[(9, 0.28097606), (10, 0.1288393), (12, 0.0797682), (13, 0.12652236), (22, 0.159377), (34, 0.17273141)]
[(4, 0.11428571), (12, 0.3419413), (22, 0.31290272), (28, 0.13245755)]


## Section 6: Storytelling

### Section 6.1: Overall Results

- Overall, our model identified 35 different topics, and the 5 most popular were news containing discussion/links to other news articles or images, the economy and finance, hillary clinton's campaign, her email server, and news articles talking about russia. Our model does a pretty good job of classifying new data into the categories established by our model previously. 

### Section 6.2: Technical and Managerial Implications:

- Based on the results of our model, we can conclude that news articles whose topics include hillary clinton's presidential campaign, her email server, the economy, russia, or lots of links or discussions about other news articles are not automatically fake news, but are potentially fake news and should be investigated further to determine if the article is indeed fake news.

### Section 6.3: Recommendation about Fake News

- I think that we have a large enough body of articles, and enough knowledge about the topics that are frequently in fake news that we could build a model that would be able to correctly use text classification to label new articles as fake news or not, with a pretty high degree of accuracy.

## Section 7: New methods

### Section 7.1: Non-negative Factorization Matrix (NMF)

In [41]:
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.decomposition import NMF, LatentDirichletAllocation

In [42]:
tfidf_vectorizer = TfidfVectorizer(max_df=0.95, min_df=2,
                                   stop_words='english')

In [43]:
for i in texts[:2]:
    print str(i)

['uuid', 'ord', 'thread', 'author', 'published', 'title', 'text', 'language', 'crawled', 'site', 'url', 'domain', 'rank', 'thread', 'title', 'spam', 'score', 'main', 'img', 'url', u'reply', 'count', u'participant', 'count', u'comment', u'share', 'type']
['bcd', 'barracuda', 'brigade', u'muslim', 'busted', 'stole', u'million', 'gov', u'benefit', 'print', 'pay', 'money', 'plus', 'interest', 'entire', 'family', 'everyone', 'came', 'deported', 'asap', 'two', 'bust', 'nhere', 'another', 'group', 'stealing', 'government', u'taxpayer', 'group', u'somali', 'stole', 'four', 'million', 'government', u'benefit', u'month', 'nwe', 'reported', 'numerous', u'case', 'muslim', u'refugee', u'immigrant', 'commit', 'fraud', 'scamming', 'system', 'control', 'related', 'english', 'percentfedup', 'com', u'muslim', 'busted', 'stole', u'million', 'gov', u'benefit', 'http', 'com', 'content', 'uploads', 'fullscreen', 'capture', 'bmp', 'jpg', 'bias']


In [44]:
texts1 = [ str(i) for i in texts]
for i in texts1[:2]:
    print i

['uuid', 'ord', 'thread', 'author', 'published', 'title', 'text', 'language', 'crawled', 'site', 'url', 'domain', 'rank', 'thread', 'title', 'spam', 'score', 'main', 'img', 'url', u'reply', 'count', u'participant', 'count', u'comment', u'share', 'type']
['bcd', 'barracuda', 'brigade', u'muslim', 'busted', 'stole', u'million', 'gov', u'benefit', 'print', 'pay', 'money', 'plus', 'interest', 'entire', 'family', 'everyone', 'came', 'deported', 'asap', 'two', 'bust', 'nhere', 'another', 'group', 'stealing', 'government', u'taxpayer', 'group', u'somali', 'stole', 'four', 'million', 'government', u'benefit', u'month', 'nwe', 'reported', 'numerous', u'case', 'muslim', u'refugee', u'immigrant', 'commit', 'fraud', 'scamming', 'system', 'control', 'related', 'english', 'percentfedup', 'com', u'muslim', 'busted', 'stole', u'million', 'gov', u'benefit', 'http', 'com', 'content', 'uploads', 'fullscreen', 'capture', 'bmp', 'jpg', 'bias']


In [48]:
tfidf = tfidf_vectorizer.fit_transform(texts1)

In [49]:
def print_top_words(model, feature_names, n_top_words):
    for topic_idx, topic in enumerate(model.components_):
        message = "Topic #%d: " % topic_idx
        message += " ".join([feature_names[i]
                             for i in topic.argsort()[:-n_top_words - 1:-1]])
        print(message)
    print()

In [52]:
nmf = NMF(n_components=35, random_state=1,
          alpha=.1, l1_ratio=.5).fit(tfidf)

print("\nTopics in NMF model (Frobenius norm):")
tfidf_feature_names = tfidf_vectorizer.get_feature_names()

n_top_words = 10

print_top_words(nmf, tfidf_feature_names, n_top_words)


Topics in NMF model (Frobenius norm):
Topic #0: xbe xbd xbb xbc xbf xba xaf xab xad pravda
Topic #1: clinton foundation campaign hillary wikileaks democratic state secretary presidential million
Topic #2: time world state government new nthe life power work law
Topic #3: trump donald supporter win republican campaign victory ntrump medium election
Topic #4: russia russian putin nato military nuclear moscow ukraine vladimir missile
Topic #5: text result italic block comment automatically bold strong formating blockquote
Topic #6: westernjournalism static earnest bias factual denial com server entirely uploads
Topic #7: que del los por para xada una como migraciones fecha
Topic #8: obama nobama administration house obamacare barack white michelle democrat nwhite
Topic #9: mosul iraqi isi force iraq city daesh civilian fighter turkey
Topic #10: election vote voter voting machine fraud poll ballot state republican
Topic #11: fbi comey investigation email clinton weiner director letter jam

In [53]:
nmf = NMF(n_components=35, random_state=1,
          beta_loss='kullback-leibler', solver='mu', max_iter=1000, alpha=.1,
          l1_ratio=.5).fit(tfidf)

print("\nTopics in NMF model (generalized Kullback-Leibler divergence):")
tfidf_feature_names = tfidf_vectorizer.get_feature_names()
n_top_words = 10

print_top_words(nmf, tfidf_feature_names, n_top_words)


Topics in NMF model (generalized Kullback-Leibler divergence):
Topic #0: xbf xbb xbe xba xbd xbc xaf http xad xab
Topic #1: time clinton nthe com new campaign hillary english nin work
Topic #2: world used time work human english life long power simply
Topic #3: trump donald win vote republican election supporter voter victory candidate
Topic #4: russia russian putin war military vladimir syria nato foreign state
Topic #5: added post comment link strong thanks write website saker leave
Topic #6: uploads http jpg english com www content twitter october static
Topic #7: que del por spanish para los xada una emtstatic este
Topic #8: obama secretary server westernjournalism clinton press white entirely party affordable
Topic #9: terrorist force report state group syria syrian killed city attack
Topic #10: vote election voter voting english com hillary clinton state presidential
Topic #11: fbi james investigation comey director case department congress email new
Topic #12: rock standing pro

### Section 7.1.1: Results of our NMF Model

- The NMF produced some interesting new topics that werent in our original LDA model. For example, this model talked about the Dakota Access Pipeline, Islam vs Christianity, and Religion whereas these were not topics in our LDA model. However, there were still some similarities, because hillary clinton was mentioned in more than one topic.

### Section 7.2: Latent Semantic Index (LSI)

Using TFIDF

In [54]:
tfidf = models.TfidfModel(corpus) # step 1 -- initialize a model

2018-10-28 15:25:02,450 : INFO : collecting document frequencies
2018-10-28 15:25:02,453 : INFO : PROGRESS: processing document #0
2018-10-28 15:25:02,661 : INFO : PROGRESS: processing document #10000
2018-10-28 15:25:02,825 : INFO : calculating IDF weights for 17949 documents and 28699 features (1880700 matrix non-zeros)


In [55]:
corpus_tfidf = tfidf[corpus]

In [57]:
numpy.random.seed(1) # setting random seed to get the same results each time. 

lsi = models.LsiModel(corpus_tfidf, id2word=dictionary, num_topics=35) # initialize an LSI transformation
corpus_lsi = lsi[corpus_tfidf] # create a double wrapper over the original corpus: bow->tfidf->fold-in-lsi

2018-10-28 15:25:43,969 : INFO : using serial LSI version on this node
2018-10-28 15:25:43,970 : INFO : updating model with new documents
2018-10-28 15:25:52,713 : INFO : preparing a new chunk of documents
2018-10-28 15:25:53,137 : INFO : using 100 extra samples and 2 power iterations
2018-10-28 15:25:53,140 : INFO : 1st phase: constructing (28700L, 135L) action matrix
2018-10-28 15:25:53,480 : INFO : orthonormalizing (28700L, 135L) action matrix
2018-10-28 15:25:55,436 : INFO : 2nd phase: running dense svd on (135L, 17949L) matrix
2018-10-28 15:25:55,596 : INFO : computing the final decomposition
2018-10-28 15:25:55,601 : INFO : keeping 35 factors (discarding 37.034% of energy spectrum)
2018-10-28 15:25:55,631 : INFO : processed documents up to #17949
2018-10-28 15:25:55,634 : INFO : topic #0(21.150): 0.797*"xbe" + 0.448*"xbd" + 0.231*"xbb" + 0.212*"xbc" + 0.190*"xbf" + 0.174*"xba" + 0.009*"xaf" + 0.005*"xad" + 0.005*"xab" + 0.003*"pravda"
2018-10-28 15:25:55,637 : INFO : topic #1(16.

In [58]:
lsi.print_topics(35)

2018-10-28 15:25:55,744 : INFO : topic #0(21.150): 0.797*"xbe" + 0.448*"xbd" + 0.231*"xbb" + 0.212*"xbc" + 0.190*"xbf" + 0.174*"xba" + 0.009*"xaf" + 0.005*"xad" + 0.005*"xab" + 0.003*"pravda"
2018-10-28 15:25:55,746 : INFO : topic #1(16.515): 0.285*"trump" + 0.265*"clinton" + 0.175*"hillary" + 0.142*"election" + 0.114*"state" + 0.112*"email" + 0.110*"russia" + 0.109*"fbi" + 0.107*"american" + 0.103*"obama"
2018-10-28 15:25:55,749 : INFO : topic #2(9.319): 0.404*"clinton" + 0.286*"fbi" + 0.241*"email" + 0.232*"hillary" + -0.200*"russia" + 0.158*"comey" + -0.157*"war" + 0.156*"investigation" + -0.142*"syria" + 0.142*"trump"
2018-10-28 15:25:55,752 : INFO : topic #3(8.244): 0.602*"trump" + -0.267*"fbi" + -0.212*"email" + -0.187*"clinton" + 0.161*"donald" + 0.152*"vote" + -0.146*"investigation" + -0.145*"comey" + -0.130*"russia" + 0.125*"election"
2018-10-28 15:25:55,755 : INFO : topic #4(7.424): 0.342*"russia" + 0.263*"trump" + 0.216*"russian" + -0.201*"text" + 0.199*"syria" + 0.149*"war"

[(0,
  u'0.797*"xbe" + 0.448*"xbd" + 0.231*"xbb" + 0.212*"xbc" + 0.190*"xbf" + 0.174*"xba" + 0.009*"xaf" + 0.005*"xad" + 0.005*"xab" + 0.003*"pravda"'),
 (1,
  u'0.285*"trump" + 0.265*"clinton" + 0.175*"hillary" + 0.142*"election" + 0.114*"state" + 0.112*"email" + 0.110*"russia" + 0.109*"fbi" + 0.107*"american" + 0.103*"obama"'),
 (2,
  u'0.404*"clinton" + 0.286*"fbi" + 0.241*"email" + 0.232*"hillary" + -0.200*"russia" + 0.158*"comey" + -0.157*"war" + 0.156*"investigation" + -0.142*"syria" + 0.142*"trump"'),
 (3,
  u'0.602*"trump" + -0.267*"fbi" + -0.212*"email" + -0.187*"clinton" + 0.161*"donald" + 0.152*"vote" + -0.146*"investigation" + -0.145*"comey" + -0.130*"russia" + 0.125*"election"'),
 (4,
  u'0.342*"russia" + 0.263*"trump" + 0.216*"russian" + -0.201*"text" + 0.199*"syria" + 0.149*"war" + 0.148*"putin" + 0.119*"clinton" + -0.109*"police" + 0.107*"nato"'),
 (5,
  u'-0.640*"que" + -0.358*"del" + -0.275*"los" + -0.229*"por" + -0.192*"para" + -0.181*"xada" + -0.169*"una" + -0.164*"

### Section 7.2.1: Results of our LSI model:

- The topics in the LSI model were also different from the LDA model. The Dakota Access pipeline was a topic in this model, and that was not in the LDA, and obama and james comey were mentioned too in connection to the 2016 election, and that was not a topic in our LDA model.

### Section 7.3: Comparing all 3 models:

- The LDA model captured different topics from the NMF and LSI models. The Dakota Access Pipeline was not in the LDA model, but it was a topic present in both the NMF and LSI models. One commonality was the mention of hillary clinton, as she appeard in a topic in some form in all 3 models. One of the ways in which she was in all 3 models was related to the 2016 election, and the belief that there was some kind of conspiracy to rig the election in her favor against donald trump.

#### On My honor as a student, I have neither given nor received any unauthorized aid on this academic work.

Eric VanMeerhaeghe